# TCC Pós Graduação Ciência de Dados e Big Data

In [8]:
import io
import os
from time import time
import requests
import pandas as pd
import numpy as np
import PyPDF2
import re

#DIR_DATASET = r'/Users/dev-rocks/Documents/TCC - Data Science e Big Data/Projeto/datasets/'
#URL_ARQUIVO_PROPOSICOES = r'http://dadosabertos.camara.leg.br/arquivos/proposicoes/csv/'
#URL_ARQUIVO_TEMAS = r'http://dadosabertos.camara.leg.br/arquivos/proposicoesTemas/csv/'

DIR_DATASET = r'C:\Users\Daniel.Vale\Personal\PBDDC\TCC\Projeto_v2\datasets\\'
URL_ARQUIVO_PROPOSICOES = r'http://dadosabertos.camara.leg.br/arquivos/proposicoes/csv/'
URL_ARQUIVO_TEMAS = r'http://dadosabertos.camara.leg.br/arquivos/proposicoesTemas/csv/'

In [372]:
def extrairDatasetsPorAno(anoInicio:int, anoFim:int):
    anosParaExtracao = range(anoInicio, anoFim+1)
    for ano in anosParaExtracao:
        urlArquivoProposicao = f'{URL_ARQUIVO_PROPOSICOES}proposicoes-{ano}.csv'
        urlArquivoTemas = f'{URL_ARQUIVO_TEMAS}proposicoesTemas-{ano}.csv'

        arquivoProposicao = requests.get(urlArquivoProposicao)
        with open(f'{DIR_DATASET}/proposicoes/proposicoes-{ano}.csv','wb') as arquivo:
            arquivo.write(arquivoProposicao.content)
            print(f'[OK    ] Arquivo baixado: {urlArquivoProposicao}')

        arquivoTemas = requests.get(urlArquivoTemas)
        with open(f'{DIR_DATASET}/temas/proposicoesTemas-{ano}.csv','wb') as arquivo:
            arquivo.write(arquivoProposicao.content)

        print(f'[OK    ] Arquivo baixado: {urlArquivoTemas}')
    print(f'[OK    ] Finalizada extração dos datasets de preposição e classificação temática de {anoInicio} a {anoFim}')

In [373]:
#Fazer a extração dos datasets no período de 2018 a 2021.
extrairDatasetsPorAno(2018,2021)

[OK    ] Arquivo baixado: http://dadosabertos.camara.leg.br/arquivos/proposicoes/csv/proposicoes-2018.csv
[OK    ] Arquivo baixado: http://dadosabertos.camara.leg.br/arquivos/proposicoesTemas/csv/proposicoesTemas-2018.csv
[OK    ] Arquivo baixado: http://dadosabertos.camara.leg.br/arquivos/proposicoes/csv/proposicoes-2019.csv
[OK    ] Arquivo baixado: http://dadosabertos.camara.leg.br/arquivos/proposicoesTemas/csv/proposicoesTemas-2019.csv
[OK    ] Arquivo baixado: http://dadosabertos.camara.leg.br/arquivos/proposicoes/csv/proposicoes-2020.csv
[OK    ] Arquivo baixado: http://dadosabertos.camara.leg.br/arquivos/proposicoesTemas/csv/proposicoesTemas-2020.csv
[OK    ] Arquivo baixado: http://dadosabertos.camara.leg.br/arquivos/proposicoes/csv/proposicoes-2021.csv
[OK    ] Arquivo baixado: http://dadosabertos.camara.leg.br/arquivos/proposicoesTemas/csv/proposicoesTemas-2021.csv
[OK    ]Finalizada extração dos datasets de preposição e classificação temática de 2018 a 2021


In [1]:
def gerarDataframeProposicoes():
    dfProposicoesList = []

    for arquivo in os.listdir(f'{DIR_DATASET}proposicoes/'):
        try:
            df = pd.read_csv(f'{DIR_DATASET}proposicoes/{arquivo}', sep=';', low_memory=False)
            dfProposicoesList.append(df)
            print(f'[OK    ] {arquivo}')
        except Exception as e:
            print(f'[ERRO  ] {arquivo}')
    
    return  pd.concat(dfProposicoesList)

In [9]:
def gerarDataframeTemas():
    dfTemasList = []
    for arquivo in os.listdir(f'{DIR_DATASET}temas/'):
        try:
            df = pd.read_csv(f'{DIR_DATASET}temas/{arquivo}', sep=';', low_memory=False)
            dfTemasList.append(df)
            print(f'[OK    ] {arquivo}')
        except Exception as e:
            print(f'[ERRO  ]: {arquivo}')
            
    return pd.concat(dfTemasList)

In [21]:
def tokenizarTexto(texto: str):
    try:
        pontuacao = ['{', '}','(', ')', ';', ':', '[', ']', ',', '-','_', '.', '$', '!', '°', '§', 'º', '/', '"', '\'','~','Ł','·','&']
        texto = texto.replace('\\n', ' ')
        
        for ponto in pontuacao:
            texto = texto.replace(ponto, ' ')

        for numero in range(0, 10):
            texto = texto.replace(str(numero), ' ')

        stopWords = pd.read_csv(f'{DIR_DATASET}stop_words.csv', usecols=['stop_words']) \
        .replace(to_replace=[r"\\t|\\n|\\r", "\t|\n|\r"], value=["", ""])
        listaStopWords = stopWords['stop_words'].values.tolist()
        tokens = texto.strip().split()
        palavrasChave = [palavra for palavra in tokens if not palavra.lower() in listaStopWords and not palavra in pontuacao]

        return ' '.join(palavrasChave)
    except Exception as e:
        print(f'[ERRO  ] Erro ao tokenizar texto: "{texto}" \n{e}')
        raise e

In [35]:
def extrairInteiroTeorPdf(conteudo):
    textoPaginas = ''
    pdf = io.BytesIO(conteudo)
    pdfReader = PyPDF2.PdfFileReader(pdf)
    numeroPaginas = pdfReader.numPages

    for p in range(numeroPaginas):
        pagina = pdfReader.getPage(p)
        textoPaginas += pagina.extractText()
  
    textoNormalizado = normalizarTeorPreposicao(textoPaginas)
    return textoNormalizado

In [38]:
def extrairInteiroTeorHtml(conteudo):
    TAG_HTML = re.compile(r'<[^>]+>')
    return TAG_HTML.sub('',conteudo)

In [30]:
dfProposicoes = gerarDataframeProposicoes()
dfProposicoes[['id','ementa']]


[ERRO  ] inteiro_teor
[OK    ] proposicoes-2018.csv
[OK    ] proposicoes-2019.csv
[OK    ] proposicoes-2020.csv
[OK    ] proposicoes-2021.csv


id                                             ementa
0      2165076  Parecer do Relator, Dep. Vinicius Carvalho (PR...
1      2167552  Parecer do Relator, Dep. Pedro Uczai (PT-SC), ...
2      2167553  Parecer do Relator, Dep. Pedro Uczai (PT-SC), ...
3      2167556  Disciplina o disposto nas Emendas Constitucion...
4      2167557  Comunica o Excelentíssimo Senhor Presidente da...
...        ...                                                ...
39737  2313785  Altera a Lei Complementar nº 130, de 17 de abr...
39738  2313786  Institui o Programa de Reescalonamento do Paga...
39739  2314174  Parecer do Relator, Dep. Felício Laterça, pela...
39740  2314175                                                NaN
39741  2314343  Emendas do Senado ao Projeto de Lei de Convers...

[126372 rows x 2 columns]

In [31]:
dfTemas = gerarDataframeTemas()
dfTemas

[OK    ] proposicoesTemas-2018.csv
[OK    ] proposicoesTemas-2019.csv
[OK    ] proposicoesTemas-2020.csv
[OK    ] proposicoesTemas-2021.csv


uriProposicao siglaTipo  numero  \
0      https://dadosabertos.camara.leg.br/api/v2/prop...       PLV       1   
1      https://dadosabertos.camara.leg.br/api/v2/prop...       PLV       1   
2      https://dadosabertos.camara.leg.br/api/v2/prop...       PLV       1   
3      https://dadosabertos.camara.leg.br/api/v2/prop...       PLV       1   
4      https://dadosabertos.camara.leg.br/api/v2/prop...       PLV       2   
...                                                  ...       ...     ...   
14898  https://dadosabertos.camara.leg.br/api/v2/prop...        PL    4600   
14899  https://dadosabertos.camara.leg.br/api/v2/prop...        PL    4600   
14900  https://dadosabertos.camara.leg.br/api/v2/prop...        PL    4601   
14901  https://dadosabertos.camara.leg.br/api/v2/prop...        PL    4601   
14902  https://dadosabertos.camara.leg.br/api/v2/prop...        PL    4602   

        ano  codTema                                         tema  relevancia  
0      2018       34                        Administração Pública           0  
1      2018       44                  Direitos Humanos e Minorias           0  
2      2018       66               Indústria, Comércio e Serviços           0  
3      2018       40                                     Economia           0  
4      2018       64  Agricultura, Pecuária, Pesca e Extrativismo           0  
...     ...      ...                                          ...         ...  
14898  2021       40                                     Economia           0  
14899  2021       70                Finanças Públicas e Orçamento           0  
14900  2021       42             Direito Civil e Processual Civil           0  
14901  2021       52             Previdência e Assistência Social           0  
14902  2021       43             Direito Penal e Processual Penal           0  

[53250 rows x 7 columns]

In [28]:
dfInteiroTeor = dfProposicoes.loc[:,['id','urlInteiroTeor']]
dfInteiroTeor.loc[:,'statusExtracao'] = 0
dfInteiroTeor.loc[:,'tipoDocumento'] = np.NaN
dfInteiroTeor.loc[:,'tamanhoEmBytes'] = 0
dfInteiroTeor.loc[:,'inteiroTeor'] = np.NaN
dfInteiroTeor.loc[:,'tokensInteiroTeor'] = np.NaN


In [29]:
dfInteiroTeor.describe()

id  statusExtracao  tipoDocumento  tamanhoEmBytes  \
count  1.263720e+05        126372.0            0.0        126372.0   
mean   2.241696e+06             0.0            NaN             0.0   
std    4.664421e+04             0.0            NaN             0.0   
min    3.088800e+05             0.0            NaN             0.0   
25%    2.205276e+06             0.0            NaN             0.0   
50%    2.243218e+06             0.0            NaN             0.0   
75%    2.278596e+06             0.0            NaN             0.0   
max    2.314512e+06             0.0            NaN             0.0   

       inteiroTeor  tokensInteiroTeor  
count          0.0                0.0  
mean           NaN                NaN  
std            NaN                NaN  
min            NaN                NaN  
25%            NaN                NaN  
50%            NaN                NaN  
75%            NaN                NaN  
max            NaN                NaN

In [34]:
#Salvar datasets consolidados em um arquivo csv
dfProposicoes.to_csv(f'{DIR_DATASET}/proposicoes.csv',index=False,sep=';',quoting=csv.QUOTE_ALL,  escapechar="\\")
print(f'[OK    ] Arquivo salvo: {DIR_DATASET}/proposicoes.csv')

dfTemas.to_csv(f'{DIR_DATASET}/temas.csv',index=False,sep=';',quoting=csv.QUOTE_ALL,  escapechar="\\")
print(f'[OK    ] Arquivo salvo: {DIR_DATASET}/temas.csv')

dfInteiroTeor.to_csv(f'{DIR_DATASET}/inteiroTeor.csv',index=False,sep=';',quoting=csv.QUOTE_ALL,  escapechar="\\")
print(f'[OK    ] Arquivo salvo: {DIR_DATASET}/inteiroTeor.csv')

[OK    ] Arquivo salvo: C:\Users\Daniel.Vale\Personal\PBDDC\TCC\Projeto_v2\datasets\\/proposicoes.csv
[OK    ] Arquivo salvo: C:\Users\Daniel.Vale\Personal\PBDDC\TCC\Projeto_v2\datasets\\/temas.csv
[OK    ] Arquivo salvo: C:\Users\Daniel.Vale\Personal\PBDDC\TCC\Projeto_v2\datasets\\/inteiroTeor.csv


## Extrair inteiro teor das proposições

In [73]:
def extrairInteiroTeor(df, qtdLimite=0):
    sessao = requests.Session()
    contador = 0
    t0 = time()
    for index,linha in df.iterrows():
        try:
            url = linha['urlInteiroTeor']
            idPreposicao = linha['id']
            indexPreposicao =  dfInteiroTeor.loc[dfInteiroTeor['id']==idPreposicao].index.item()

            if contador%100==0:
                print(f'[INFO  ] [{indexPreposicao}][{idPreposicao}][{url}]')

            if type(url) == float:
                dfInteiroTeor.loc[index,['statusExtracao','tipoDocumento']] = [4,'Proposicao s/ url inteiro teor']
                continue

            response = sessao.get(url)
            headers = response.headers
            tipoDocumento = str(headers['content-type'])
            statusExtracao=0
            inteiroTeor =''
            tokensInteiroTeor = ''
            tamanhoConteudo = 0

            if tipoDocumento =='application/pdf':
                inteiroTeor = extrairInteiroTeorPdf(response.content)
                statusExtracao = 1
            elif tipoDocumento=='text/html;charset=utf-8':
                idTeor = url.split('=')[-1]
                response = sessao.get(f'https://www.camara.leg.br/internet/ordemdodia/integras/{idTeor}.htm')
                inteiroTeor = extrairInteiroTeorHtml(response.text)
                statusExtracao = 1
            else:
                print(f'[ALERTA] [{url}]{tipoDocumento}')
                statusExtracao = 2

            
            tokensInteiroTeor = tokenizarTexto(inteiroTeor)
            df.loc[indexPreposicao,
                              ['statusExtracao',
                               'tipoDocumento',
                               'inteiroTeor',
                               'tokenInteiroTeor',
                               'tamanhoEmBytes']] = [statusExtracao,tipoDocumento,inteiroTeor]
            
            if qtdLimite>0 and contador ==qtdLimite:
                break
            
            contador+=1
        except Exception as e:
            print(f'[ERRO  ] Erro no indice: {index} {e.args}')
            df.loc[indexPreposicao,['statusExtracao','tipoDocumento']] = [3,e.args]


    sesssao.close()
    duracao = time()-t0

    print(f'[INFO  ] Extraído teor de {contador} proposicoes em {duracao:.0f} segundos. Media={(duracao/contador):.2f}/s' )
    df.to_csv(f'{DIR_DATASET}/inteiroTeor.csv',index=False,sep=';',quoting=csv.QUOTE_ALL,  escapechar="\\")


In [68]:
dfInteiroTeor = pd.read_csv(f'{DIR_DATASET}inteiroTeor.csv', sep=';', low_memory=False)
dfInteiroTeor.describe()

id  statusExtracao  tipoDocumento  tamanhoEmBytes  \
count  1.263720e+05        126372.0            0.0        126372.0   
mean   2.241696e+06             0.0            NaN             0.0   
std    4.664421e+04             0.0            NaN             0.0   
min    3.088800e+05             0.0            NaN             0.0   
25%    2.205276e+06             0.0            NaN             0.0   
50%    2.243218e+06             0.0            NaN             0.0   
75%    2.278596e+06             0.0            NaN             0.0   
max    2.314512e+06             0.0            NaN             0.0   

       inteiroTeor  tokensInteiroTeor  
count          0.0                0.0  
mean           NaN                NaN  
std            NaN                NaN  
min            NaN                NaN  
25%            NaN                NaN  
50%            NaN                NaN  
75%            NaN                NaN  
max            NaN                NaN

In [69]:
dfSemUrlInteiroTeor = dfInteiroTeor.index[dfInteiroTeor['urlInteiroTeor'].isnull()]
print(f'[INFO    ] Total de proposições sem inteiro teor: {len(dfSemUrlInteiroTeor)}')

dfInteiroTeor.loc[dfInteiroTeor['urlInteiroTeor'].isnull(),
                 ['statusExtracao','tipoDocumento']] = [4,'Proposicao s/ url inteiro teor']

dfInteiroTeor.loc[dfInteiroTeor['statusExtracao']==4]


[INFO    ] Total de proposições sem inteiro teor: 636


id urlInteiroTeor  statusExtracao  \
994     2169023            NaN               4   
1144    2169250            NaN               4   
4333    2173220            NaN               4   
4334    2173221            NaN               4   
4481    2173402            NaN               4   
...         ...            ...             ...   
124939  2312236            NaN               4   
125180  2312500            NaN               4   
125181  2312501            NaN               4   
125559  2312911            NaN               4   
125582  2312942            NaN               4   

                         tipoDocumento  tamanhoEmBytes  inteiroTeor  \
994     Proposicao s/ url inteiro teor               0          NaN   
1144    Proposicao s/ url inteiro teor               0          NaN   
4333    Proposicao s/ url inteiro teor               0          NaN   
4334    Proposicao s/ url inteiro teor               0          NaN   
4481    Proposicao s/ url inteiro teor               0          NaN   
...                                ...             ...          ...   
124939  Proposicao s/ url inteiro teor               0          NaN   
125180  Proposicao s/ url inteiro teor               0          NaN   
125181  Proposicao s/ url inteiro teor               0          NaN   
125559  Proposicao s/ url inteiro teor               0          NaN   
125582  Proposicao s/ url inteiro teor               0          NaN   

        tokensInteiroTeor  
994                   NaN  
1144                  NaN  
4333                  NaN  
4334                  NaN  
4481                  NaN  
...                   ...  
124939                NaN  
125180                NaN  
125181                NaN  
125559                NaN  
125582                NaN  

[636 rows x 7 columns]

In [71]:
dfParaExtracao = dfInteiroTeor.loc[dfInteiroTeor['statusExtracao']==0]
print(f'[INFO    ] Proposicoes para extracao de inteiro teor: {len(dfParaExtracao)}')

[INFO    ] Proposicoes para extracao de inteiro teor: 125736


In [72]:
extrairInteiroTeor(dfParaExtracao,5000)

[INFO  ] [0][2165076][http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1692486]
[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1692486]text/html
[ERRO  ] Erro no indice: 0 ('Must have equal len keys and value when setting with an iterable',)
[INFO  ] [1][2167552][http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637461]
[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637461]text/html
[ERRO  ] Erro no indice: 1 ('Must have equal len keys and value when setting with an iterable',)
[INFO  ] [2][2167553][http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637462]
[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637462]text/html
[ERRO  ] Erro no indice: 2 ('Must have equal len keys and value when setting with an iterable',)
[INFO  ] [3][2167556][http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637536]
[ALERTA] [http://www.cama

c:\program files\python39\lib\site-packages\numpy\core\fromnumeric.py:3199: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  return asarray(a).ndim
c:\program files\python39\lib\site-packages\numpy\core\fromnumeric.py:3199: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  return asarray(a).ndim
c:\program files\python39\lib\site-packages\numpy\core\fromnumeric.py:3199: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you m

[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637611]text/html
[ERRO  ] Erro no indice: 4 ('Must have equal len keys and value when setting with an iterable',)
[INFO  ] [5][2167558][http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637640]
[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637640]text/html
[ERRO  ] Erro no indice: 5 ('Must have equal len keys and value when setting with an iterable',)
[INFO  ] [6][2167559][http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637689]
[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637689]text/html
[ERRO  ] Erro no indice: 6 ('Must have equal len keys and value when setting with an iterable',)
[INFO  ] [7][2167561][http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637717]
[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637717]text/html
[ERRO  ] Erro no indice: 7 (

c:\program files\python39\lib\site-packages\numpy\core\fromnumeric.py:3199: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  return asarray(a).ndim
c:\program files\python39\lib\site-packages\numpy\core\fromnumeric.py:3199: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  return asarray(a).ndim
c:\program files\python39\lib\site-packages\numpy\core\fromnumeric.py:3199: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you m

[ERRO  ] Erro no indice: 8 ('Must have equal len keys and value when setting with an iterable',)
[INFO  ] [9][2167563][http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637720]
[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637720]text/html
[ERRO  ] Erro no indice: 9 ('Must have equal len keys and value when setting with an iterable',)
[INFO  ] [10][2167564][http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637822]
[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637822]text/html
[ERRO  ] Erro no indice: 10 ('Must have equal len keys and value when setting with an iterable',)
[INFO  ] [11][2167565][http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637823]
[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1637823]text/html
[ERRO  ] Erro no indice: 11 ('Must have equal len keys and value when setting with an iterable',)
[INFO  ] [12][2167566][

...

[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1664002]text/html
[ERRO  ] Erro no indice: 7516 ('Must have equal len keys and value when setting with an iterable',)
[INFO  ] [7517][2176997][http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1664002]
[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1664002]text/html
[ERRO  ] Erro no indice: 7517 ('Must have equal len keys and value when setting with an iterable',)
[INFO  ] [7518][2176998][http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1664002]
[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1664002]text/html
[ERRO  ] Erro no indice: 7518 ('Must have equal len keys and value when setting with an iterable',)
[INFO  ] [7519][2176999][http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1664004]
[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1664004]text/html
[ERRO  ] E

c:\program files\python39\lib\site-packages\numpy\core\fromnumeric.py:3199: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  return asarray(a).ndim
c:\program files\python39\lib\site-packages\numpy\core\fromnumeric.py:3199: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  return asarray(a).ndim
c:\program files\python39\lib\site-packages\numpy\core\fromnumeric.py:3199: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you m

[ERRO  ] Erro no indice: 7521 ('Must have equal len keys and value when setting with an iterable',)
[INFO  ] [7522][2177002][http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1664011]
[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1664011]text/html
[ERRO  ] Erro no indice: 7522 ('Must have equal len keys and value when setting with an iterable',)
[INFO  ] [7523][2177003][http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1664012]
[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1664012]text/html
[ERRO  ] Erro no indice: 7523 ('Must have equal len keys and value when setting with an iterable',)
[INFO  ] [7524][2177004][http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1664013]
[ALERTA] [http://www.camara.gov.br/proposicoesWeb/prop_mostrarintegra?codteor=1664013]text/html
[ERRO  ] Erro no indice: 7524 ('Must have equal len keys and value when setting with an iterable',)
[INFO 

c:\program files\python39\lib\site-packages\numpy\core\fromnumeric.py:3199: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  return asarray(a).ndim
c:\program files\python39\lib\site-packages\numpy\core\fromnumeric.py:3199: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  return asarray(a).ndim
c:\program files\python39\lib\site-packages\numpy\core\fromnumeric.py:3199: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you m

KeyboardInterrupt: 

In [ ]:
dfInteiroTeor = pd.read_csv(f'{DIR_DATASET}inteiroTeor.csv', sep=';', low_memory=False)